In [1]:
import numpy as np


context_dimension  = 2
graph_db_path      = 'word_graph' 


#def get_corpus(text_file):
    
    #filter_text() #only keep ([a-z],[0-9],{'.' ,',','!'})
    
    #return corpus #list of words


def get_ngram(indices, window_size = 2):  
    ngrams = []
    count  = 0
    for token in indices[:len(indices)-window_size+1]:
        ngrams.append(indices[count:count+window_size])  
        count = count+1  
    return ngrams

        

def touch_graph(graph,word):
    if word not in graph['words'].keys():
        graph['words'][word] = {'frequency':1 ,'connections':{} }
        
    else :
        graph['words'][word]['frequency'] += 1
    
    return graph
 
    
def touch_connection(graph,word_1,word_2):
    if word_2 not in graph['words'][word_1]['connections'].keys():
        context_vector      =  np.random.rand(context_dimension)
        unit_context_vector = context_vector / np.linalg.norm(context_vector)
        graph['words'][word_1]['connections'][word_2] = {'frequency':1 , 'context' : list(unit_context_vector) , 'update_count':0 , 'lock':False}
    else:
        graph['words'][word_1]['connections'][word_2]['frequency'] += 1
    return graph

def update_graph(corpus,graph=None):
    if graph == None:
        graph = {'words':{}}
    ngram = get_ngram(range(len(corpus)) ,2)
    for pair_index ,pair in  enumerate(ngram) :
        word_1 = corpus[pair[0]]
        word_2 = corpus[pair[1]]
        #print(pair_index,pair)
        if pair_index ==0 :
            graph = touch_graph(graph, word_1)
        graph = touch_graph(graph,word_2)
        graph = touch_connection(graph,word_1,word_2)
        
    return graph            





In [2]:
sample_text_path = '/home/dhiraj/Documents/stuff/word-tree/sample_text.txt'

In [3]:
corpus_text = open(sample_text_path).read()
corpus_text = corpus_text.replace(',' ,'')
corpus_text = corpus_text.replace('.' ,'')

corpus = corpus_text.split(' ')
corpus[:5]

['You', 'are', 'given', 'a', 'rotation']

In [4]:
import pyperclip
import json

graph = update_graph(corpus)
pyperclip.copy(json.dumps(graph))
#graph

In [46]:


def get_ngram(indices, window_size = 2):  
    ngrams = []
    count  = 0
    for token in indices[:len(indices)-window_size+1]:
        ngrams.append(indices[count:count+window_size])  
        count = count+1  
    return ngrams

      

def touch_graph_db(collection,word):
    
    find_word = collection.find_one({'word':word})
    if find_word == None:
        print('new owrd !!!' , word)
        collection.insert_one( { 'word':word, 'frequency':1 ,'connections': [] })
    else :
        print('word node present',word)
        frequecny = find_word['frequency'] 
        collection.update_one({'word':word}, {"$set" : {'frequency' : frequecny + 1}})

    
def touch_connection_db(collection,word_1,word_2):
    
    find_connection = collection.find_one({'word': word_1,'connections.word': word_2}})
    
    if find_connection == None:
        context_vector      =  np.random.rand(context_dimension)
        unit_context_vector = context_vector / np.linalg.norm(context_vector)
        connection          = {'word':word_2 , \
                               'frequency':1 ,\
                               'context' : unit_context_vector , \
                               'update_count':0 , \
                               'lock':False}
        
        collection.update_one({'word':word_1}, {'$push' : {'connections' : connection}})       
    else:
        frequecny = ['frequency']
        update_key = 'connections.' + str(word_2) + '.frequency'
        collection.update_one({'word':word_1} ,{'$set': {update_key: frequecny +1 }})
        collection.find_one({'word':word_1 ,'connections' :{}})['frequency']



def update_graph_db(corpus,collection):
    
    ngram = get_ngram(range(len(corpus)) ,2)
    
    for pair_index ,pair in  enumerate(ngram) :
        word_1 = corpus[pair[0]]
        word_2 = corpus[pair[1]]
        if pair_index ==0 :
            touch_graph_db(collection, word_1)
        touch_graph_db(collection,word_2)
        touch_connection_db(collection,word_1,word_2)
       

In [16]:

def get_ngram(indices, window_size = 2):  
    ngrams = []
    count  = 0
    for token in indices[:len(indices)-window_size+1]:
        ngrams.append(indices[count:count+window_size])  
        count = count+1  
    return ngrams

      


    
def touch_connection_db(collection,word_1,word_2):
    
    find_connection = collection.find_one({'word': word_1,'connection': word_2})
    
    if find_connection == None:
        #print('connection {} {} is new'.format(word_1,word_2))
        context_vector      =  np.random.rand(context_dimension)
        unit_context_vector = context_vector / np.linalg.norm(context_vector)
        connection          = {'word':word_1 , \
                               'connection': word_2,\
                               'frequency':1 ,\
                               'context' : list(unit_context_vector) , \
                               'update_count':0 , \
                               'lock':False}
        
        collection.insert_one(connection)       
    else:
        #print('connection {} {} is old'.format(word_1,word_2))
        frequecny = find_connection['frequency']
        collection.update_one({'word': word_1,'connection': word_2} \
                              ,{'$set': {'frequency': frequecny +1 }})
        


def update_graph_db(corpus,collection):
    
    ngram = get_ngram(range(len(corpus)) ,2)
    
    for pair_index ,pair in  enumerate(ngram) :
        word_1 = corpus[pair[0]]
        word_2 = corpus[pair[1]]
        touch_connection_db(collection,word_1,word_2)
        print((index / len(corpus)) * 100 ) 

In [52]:
sample_text_path = '/home/dhiraj/Documents/stuff/word_tree/sample_text.txt'

In [53]:
corpus_text = open(sample_text_path).read()
corpus_text = corpus_text.replace(',' ,'')
corpus_text = corpus_text.replace('.' ,'')

corpus = corpus_text.split(' ')
corpus[:5]

['You', 'are', 'given', 'a', 'rotation']

In [48]:
#import pyperclip
#import json

#graph = update_graph(corpus)
#pyperclip.copy(json.dumps(graph))

In [49]:
#corpus = ['You','who']

In [54]:
import pymongo

myclient = pymongo.MongoClient('mongodb://localhost:27017')

mydb = myclient["mydatabase"]
words = mydb.word3

In [55]:
context_dimension  = 75

update_graph_db(corpus,words)

In [30]:
for connection in words.find({'word':'set'}):
    print(connection)

{'_id': ObjectId('5fba95f02077310ef600d37f'), 'word': 'set', 'connection': 'since', 'frequency': 1, 'context': [0.9525462204761543, 0.30439398459331213], 'update_count': 0, 'lock': False}
{'_id': ObjectId('5fba95f02077310ef600d397'), 'word': 'set', 'connection': 'of', 'frequency': 4, 'context': [0.8942630678126893, 0.4475416914056584], 'update_count': 0, 'lock': False}
{'_id': ObjectId('5fba95f02077310ef600d3c7'), 'word': 'set', 'connection': 'freely', 'frequency': 1, 'context': [0.46091421980132585, 0.8874446923526756], 'update_count': 0, 'lock': False}
{'_id': ObjectId('5fba95f02077310ef600d3dc'), 'word': 'set', 'connection': 'structure', 'frequency': 2, 'context': [0.6944520411527697, 0.7195389930634417], 'update_count': 0, 'lock': False}
{'_id': ObjectId('5fba95f02077310ef600d3f2'), 'word': 'set', 'connection': 'prediction', 'frequency': 1, 'context': [0.6571424849815212, 0.7537663792132887], 'update_count': 0, 'lock': False}


In [33]:
pd.DataFrame(words.find({'word':'set'}))

_id word  connection  frequency  \
0  5fba95f02077310ef600d37f  set       since          1   
1  5fba95f02077310ef600d397  set          of          4   
2  5fba95f02077310ef600d3c7  set      freely          1   
3  5fba95f02077310ef600d3dc  set   structure          2   
4  5fba95f02077310ef600d3f2  set  prediction          1   

                                     context  update_count   lock  
0  [0.9525462204761543, 0.30439398459331213]             0  False  
1   [0.8942630678126893, 0.4475416914056584]             0  False  
2  [0.46091421980132585, 0.8874446923526756]             0  False  
3   [0.6944520411527697, 0.7195389930634417]             0  False  
4   [0.6571424849815212, 0.7537663792132887]             0  False

In [17]:
import pandas as pd
import re

In [26]:
sample_text_path = '/home/dhiraj/Documents/stuff/word_tree/data/pride_and_prejudice_cleaned.txt'

In [27]:
corpus_text = open(sample_text_path).read()

In [28]:
corpus_text = corpus_text.replace('\n' , '')
match = re.search('  ', corpus_text)
while match!= None:
    corpus_text = corpus_text.replace('  ', ' ')
    match = re.search('  ',corpus_text)
    print( '__ found' )

__ found
__ found
__ found
__ found


In [29]:
len(corpus_text)

676389

In [22]:
corpus = corpus_text.split(' ')

In [23]:
corpus[:5]

['It', 'is', 'a', 'truth', 'universally']

In [24]:
import pymongo
import time
myclient = pymongo.MongoClient('mongodb://localhost:27017')

mydb = myclient["mydatabase"]
words = mydb.p_and_p

In [25]:
start = time.time()
context_dimension  = 75

update_graph_db(corpus,words)

end = time.time() - start

connection It is is new
connection is a is new
connection a truth is new
connection truth universally is new
connection universally acknowledged is new
connection acknowledged , is new
connection , that is new
connection that a is new
connection a single is new
connection single man is new
connection man in is new
connection in possession is new
connection possession of is new
connection of a is new
connection a good is new
connection good fortune is new
connection fortune , is new
connection , must is new
connection must be is new
connection be in is new
connection in want is new
connection want of is new
connection of a is old
connection a wife is new
connection wife . is new
connection . However is new
connection However little is new
connection little known is new
connection known the is new
connection the feelings is new
connection feelings or is new
connection or views is new
connection views of is new
connection of such is new
connection such a is new
connection a man is new
con

connection as you is new
connection you are is new
connection are as is new
connection as handsome is new
connection handsome as is new
connection as any is new
connection any of is new
connection of them is old
connection them , is old
connection , Mr is new
connection Mr . is old
connection . Bingley is new
connection Bingley may is new
connection may like is new
connection like you is new
connection you the is new
connection the best is new
connection best of is new
connection of the is old
connection the party is new
connection party . is new
connection . My is old
connection My dear is old
connection dear , is old
connection , you is old
connection you flatter is new
connection flatter me is new
connection me . is new
connection . I is old
connection I certainly is new
connection certainly _have_ is new
connection _have_ had is new
connection had my is new
connection my share is new
connection share of is new
connection of beauty is new
connection beauty , is new
connection , but 

connection have a is new
connection a high is new
connection high respect is new
connection respect for is new
connection for your is new
connection your nerves is new
connection nerves . is old
connection . They is old
connection They are is new
connection are my is new
connection my old is new
connection old friends is new
connection friends . is new
connection . I is old
connection I have is old
connection have heard is new
connection heard you is new
connection you mention is new
connection mention them is new
connection them with is new
connection with consideration is new
connection consideration these is new
connection these last is new
connection last twenty is new
connection twenty years is new
connection years at is new
connection at least is new
connection least . is new
connection . Ah is new
connection Ah , is new
connection , you is old
connection you do is old
connection do not is old
connection not know is new
connection know what is new
connection what I is new
connect

connection , and is old
connection and I is old
connection I have is old
connection have no is old
connection no opinion is new
connection opinion of is new
connection of her is old
connection her . is new
connection . No is new
connection No more is new
connection more have is new
connection have I is new
connection I , is new
connection , said is old
connection said Mr is new
connection Mr . is old
connection . Bennet is old
connection Bennet ; is new
connection ; and is old
connection and I is old
connection I am is old
connection am glad is new
connection glad to is old
connection to find is new
connection find that is new
connection that you is new
connection you do is old
connection do not is old
connection not depend is new
connection depend on is new
connection on her is new
connection her serving is new
connection serving you is new
connection you . is old
connection . Mrs is new
connection Mrs . is old
connection . Bennet is old
connection Bennet deigned is new
connection dei

connection cried he is new
connection he . is new
connection . Do is old
connection Do you is old
connection you consider is new
connection consider the is new
connection the forms is new
connection forms of is new
connection of introduction is new
connection introduction , is new
connection , and is old
connection and the is old
connection the stress is new
connection stress that is new
connection that is is new
connection is laid is new
connection laid on is new
connection on them is new
connection them , is old
connection , as is old
connection as nonsense is new
connection nonsense ? is new
connection ? I is old
connection I cannot is new
connection cannot quite is new
connection quite agree is new
connection agree with is new
connection with you is new
connection you _there_ is new
connection _there_ . is new
connection . What is old
connection What say is new
connection say you is new
connection you , is new
connection , Mary is new
connection Mary ? is new
connection ? For is ne

...

connection was managed is new
connection managed ? is new
connection ? No is old
connection No really is new
connection really , is old
connection , replied is old
connection replied Elizabeth is old
connection Elizabeth ; is old
connection ; I is old
connection I think is old
connection think there is old
connection there cannot is old
connection cannot be is old
connection be too is old
connection too little is old
connection little said is new
connection said on is new
connection on the is old
connection the subject is old
connection subject . is old
connection . La is old
connection La ! is old
connection ! You is old
connection You are is old
connection are so is old
connection so strange is new
connection strange ! is old
connection ! But is old
connection But I is old
connection I must is old
connection must tell is new
connection tell you is old
connection you how is old
connection how it is old
connection it went is old
connection went off is old
connection off . is old
connec

connection away upon is new
connection upon business is new
connection business to is old
connection to that is old
connection that horrid is new
connection horrid man is old
connection man Mr is new
connection Mr . is old
connection . Stone is new
connection Stone . is new
connection . And is old
connection And then is old
connection then , is old
connection , you is old
connection you know is old
connection know , is old
connection , when is old
connection when once is old
connection once they is old
connection they get is old
connection get together is new
connection together , is old
connection , there is old
connection there is is old
connection is no is old
connection no end is new
connection end of is old
connection of it is old
connection it . is old
connection . Well is old
connection Well , is old
connection , I is old
connection I was is old
connection was so is old
connection so frightened is new
connection frightened I is new
connection I did is old
connection did not is o

connection exactly a is new
connection a scene is new
connection scene , is old
connection , and is old
connection and exactly is new
connection exactly among is new
connection among people is new
connection people , is old
connection , where is old
connection where he is old
connection he had is old
connection had apparently is new
connection apparently least is new
connection least to is old
connection to do is old
connection do , is old
connection , and is old
connection and least is new
connection least temptation is new
connection temptation to is old
connection to go is old
connection go . is old
connection . Conjectures is new
connection Conjectures as is new
connection as to is old
connection to the is old
connection the meaning is old
connection meaning of is old
connection of it is old
connection it , is old
connection , rapid is new
connection rapid and is new
connection and wild is old
connection wild , is old
connection , hurried is old
connection hurried into is old
conne

connection her letter is old
connection letter as is new
connection as soon is old
connection soon as is old
connection as she is old
connection she possibly is new
connection possibly could is new
connection could . is old
connection . She is old
connection She was is old
connection was no is old
connection no sooner is old
connection sooner in is new
connection in possession is old
connection possession of is old
connection of it is old
connection it than is old
connection than , is new
connection , hurrying is new
connection hurrying into is new
connection into the is old
connection the little is old
connection little copse is old
connection copse , is new
connection , where is old
connection where she is old
connection she was is old
connection was least is old
connection least likely is new
connection likely to is old
connection to be is old
connection be interrupted is new
connection interrupted , is new
connection , she is old
connection she sat is old
connection sat down is old

KeyboardInterrupt: 

In [12]:
import numpy as np